In [1]:
# flatly, lumen, sandstone, yeti
#import pandas as pd
import polars as pl
from great_tables import GT, _data_color, md, nanoplot_options
from IPython.display import Markdown

In [2]:
df = pl.read_parquet(
    f"./data/arrivals_polars.parquet"
).sort("caltrans_district", "n_trips", descending=[False, False])

In [3]:
all_districts = sorted(df.get_column("caltrans_district").unique())

In [4]:
def get_hex(color_name: str) -> str:
    """
    Since some of the color names don't pull the hex code, 
    we'll grab it here.
    """
    return _data_color.constants.COLOR_NAME_TO_HEX[color_name]

nano_options = nanoplot_options(
    data_point_radius=0,
    data_point_stroke_color="none",
    data_point_stroke_width=0,
    data_line_type="curved",
    data_line_stroke_color=get_hex("steelblue4"),
    data_line_stroke_width=8,
    data_area_fill_color=get_hex("steelblue4"),
    #vertical_guide_stroke_color=None,
    show_y_axis_guide=True,
    #show_vertical_guides=False,
    interactive_data_values = True,
    #reference_line_color=get_hex("salmon1"),
    show_reference_line=False
)

In [5]:
# https://quarto.org/docs/output-formats/html-themes.html
# https://github.com/posit-dev/great-tables/blob/main/great_tables/_data_color/constants.py
def make_plot(df):
    table = (GT(df)
     #.data_color(
     #    columns = ["caltrans_district"],
     #    palette = "Pastel1"
     #)
    .fmt_integer(
          columns = ["n_trips"]
     ).data_color(
        columns=["n_trips"],
        palette=["white", "steelblue"],
        na_color="lightgray"
     ).fmt_nanoplot(
         columns = "weekday_arrivals", 
         plot_type="line",
         reference_line="mean",
         options = nano_options
     ).fmt_nanoplot(
         columns = "weekend_arrivals", 
         plot_type="line",
         reference_line="mean",
         options = nano_options
     ).cols_label(
         name = "Operator",
         n_trips = "Weekly Trips",
         weekday_arrivals = "Weekday Arrivals",
         weekend_arrivals = "Weekend Arrivals",
     ).sub_missing(
         columns = ["weekday_arrivals", "weekend_arrivals"],
         missing_text = ""
     ).tab_header(
         title = "Transit Arrivals by the Hour",
         #subtitle = "weekday vs weekend totals"
     )#.tab_source_note(
      #   source_note = "GTFS scheduled stop_times.txt"
     #).tab_source_note(
      #  source_note = md(
      #      "[GTFS specification](https://gtfs.org/schedule/reference/#stop_timestxt)"
      #  )
     #)
    .tab_options(
        container_width = "100%",
        table_background_color="white",
        table_body_hlines_style="none",
        table_body_vlines_style="none",
        heading_background_color="white",
        column_labels_background_color="white",
        row_group_background_color="white",
        stub_background_color="white",
        source_notes_background_color="white"
     )
    .cols_hide("caltrans_district")
    )
    return table

In [6]:
def district_plot(district_name: str):
    display(Markdown(f"## {district_name}"))
    table = make_plot(df.filter(pl.col("caltrans_district") == district_name))
    display(table)

In [7]:
intro_paragraph = (
    "How does transit service breakdown by the hour? "
    "While transit operators typically operate at higher frequencies during peak "
    "commuting hours, there might be differences across operators. "
    "Some operators might have fairly consistent midday service while others "
    "operate primarily during peak hours or only certain hours of the day. "
    "We can use GTFS scheduled stop times to count the number of arrivals " 
    "for each hour of the day and aggregate that to weekday vs weekends. "
)

In [8]:
Markdown(intro_paragraph)

How does transit service breakdown by the hour? While transit operators typically operate at higher frequencies during peak commuting hours, there might be differences across operators. Some operators might have fairly consistent midday service while others operate primarily during peak hours or only certain hours of the day. We can use GTFS scheduled stop times to count the number of arrivals for each hour of the day and aggregate that to weekday vs weekends. 

References:
* [General Transit Feed Specification](https://gtfs.org/)
* [GTFS stop_times table](https://gtfs.org/schedule/reference/#stop_timestxt)

In [9]:
for d in all_districts:
    district_plot(d)

## 01 - Eureka

GT(_tbl_data=shape: (6, 5)
┌───────────────────┬──────────────────────┬─────────┬──────────────────┬──────────────────┐
│ caltrans_district ┆ name                 ┆ n_trips ┆ weekday_arrivals ┆ weekend_arrivals │
│ ---               ┆ ---                  ┆ ---     ┆ ---              ┆ ---              │
│ str               ┆ str                  ┆ i64     ┆ list[i64]        ┆ list[i64]        │
╞═══════════════════╪══════════════════════╪═════════╪══════════════════╪══════════════════╡
│ 01 - Eureka       ┆ Curry Public Transit ┆ 66      ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 01 - Eureka       ┆ Oregon POINT         ┆ 126     ┆ [10, 0, … 5]     ┆ [4, 0, … 2]      │
│ 01 - Eureka       ┆ Redwood Coast l      ┆ 329     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 01 - Eureka       ┆ Mendocino            ┆ 648     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 01 - Eureka       ┆ Lake                 ┆ 655     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 01 - Eureka       ┆ Humboldt             ┆ 839     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
└───────────────────┴──────────────────────┴─────────┴──────────────────┴──────────────────┘, _body=<great_tables._gt_data.Body object at 0x7ff256c56e10>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='left', column_width=None), ColInfo(var='name', type=<ColInfoTypeEnum.default: 1>, column_label='Operator', column_align='left', column_width=None), ColInfo(var='n_trips', type=<ColInfoTypeEnum.default: 1>, column_label='Weekly Trips', column_align='right', column_width=None), ColInfo(var='weekday_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekday Arrivals', column_align='center', column_width=None), ColInfo(var='weekend_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekend Arrivals', column_align='center', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=3, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=4, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=5, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Transit Arrivals by the Hour', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=0, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#ffffff')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=1, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#f1f5f9')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=2, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#c0d4e5')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=3, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#74a1c7')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=4, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, st

## 02 - Redding

GT(_tbl_data=shape: (8, 5)
┌───────────────────┬─────────────┬─────────┬──────────────────┬──────────────────┐
│ caltrans_district ┆ name        ┆ n_trips ┆ weekday_arrivals ┆ weekend_arrivals │
│ ---               ┆ ---         ┆ ---     ┆ ---              ┆ ---              │
│ str               ┆ str         ┆ i64     ┆ list[i64]        ┆ list[i64]        │
╞═══════════════════╪═════════════╪═════════╪══════════════════╪══════════════════╡
│ 02 - Redding      ┆ Sage Stage  ┆ 14      ┆ [0, 0, … 0]      ┆ null             │
│ 02 - Redding      ┆ Lassen Flex ┆ 54      ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 02 - Redding      ┆ Trinity     ┆ 57      ┆ [0, 0, … 0]      ┆ null             │
│ 02 - Redding      ┆ Plumas      ┆ 170     ┆ [0, 0, … 0]      ┆ null             │
│ 02 - Redding      ┆ Lassen      ┆ 177     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 02 - Redding      ┆ Siskiyou    ┆ 185     ┆ [0, 0, … 0]      ┆ null             │
│ 02 - Redding      ┆ Tehama      ┆ 327     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 02 - Redding      ┆ Redding     ┆ 1677    ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
└───────────────────┴─────────────┴─────────┴──────────────────┴──────────────────┘, _body=<great_tables._gt_data.Body object at 0x7ff256c56e10>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='left', column_width=None), ColInfo(var='name', type=<ColInfoTypeEnum.default: 1>, column_label='Operator', column_align='left', column_width=None), ColInfo(var='n_trips', type=<ColInfoTypeEnum.default: 1>, column_label='Weekly Trips', column_align='right', column_width=None), ColInfo(var='weekday_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekday Arrivals', column_align='center', column_width=None), ColInfo(var='weekend_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekend Arrivals', column_align='center', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=3, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=4, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=5, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=6, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=7, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Transit Arrivals by the Hour', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=0, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#ffffff')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=1, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#fbfcfd')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=2, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#fafcfd')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=3, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=

## 03 - Marysville

...

GT(_tbl_data=shape: (16, 5)
┌───────────────────┬──────────────────┬─────────┬──────────────────┬──────────────────┐
│ caltrans_district ┆ name             ┆ n_trips ┆ weekday_arrivals ┆ weekend_arrivals │
│ ---               ┆ ---              ┆ ---     ┆ ---              ┆ ---              │
│ str               ┆ str              ┆ i64     ┆ list[i64]        ┆ list[i64]        │
╞═══════════════════╪══════════════════╪═════════╪══════════════════╪══════════════════╡
│ 10 - Stockton     ┆ Blossom Express  ┆ 8       ┆ [0, 0, … 0]      ┆ null             │
│ 10 - Stockton     ┆ eTrans           ┆ 30      ┆ [0, 0, … 0]      ┆ null             │
│ 10 - Stockton     ┆ Bay Area 511 ACE ┆ 40      ┆ [0, 0, … 0]      ┆ null             │
│ 10 - Stockton     ┆ YARTS            ┆ 63      ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 10 - Stockton     ┆ Grapeline        ┆ 138     ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ …                 ┆ …                ┆ …       ┆ …                ┆ …                │
│ 10 - Stockton     ┆ Turlock          ┆ 1460    ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 10 - Stockton     ┆ Merced           ┆ 1941    ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 10 - Stockton     ┆ StanRTA          ┆ 2084    ┆ [0, 0, … 44]     ┆ null             │
│ 10 - Stockton     ┆ Merced GMV       ┆ 2619    ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
│ 10 - Stockton     ┆ San Joaquin      ┆ 6939    ┆ [0, 0, … 0]      ┆ [0, 0, … 0]      │
└───────────────────┴──────────────────┴─────────┴──────────────────┴──────────────────┘, _body=<great_tables._gt_data.Body object at 0x7ff2220ef650>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='left', column_width=None), ColInfo(var='name', type=<ColInfoTypeEnum.default: 1>, column_label='Operator', column_align='left', column_width=None), ColInfo(var='n_trips', type=<ColInfoTypeEnum.default: 1>, column_label='Weekly Trips', column_align='right', column_width=None), ColInfo(var='weekday_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekday Arrivals', column_align='center', column_width=None), ColInfo(var='weekend_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekend Arrivals', column_align='center', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=3, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=4, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=5, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=6, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=7, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=8, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=9, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=10, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=11, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=12, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=13, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=14, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=15, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Transit Arrivals by the Hour', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=0, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_alig

## 11 - San Diego

GT(_tbl_data=shape: (4, 5)
┌───────────────────┬─────────────────┬─────────┬───────────────────────┬─────────────────────┐
│ caltrans_district ┆ name            ┆ n_trips ┆ weekday_arrivals      ┆ weekend_arrivals    │
│ ---               ┆ ---             ┆ ---     ┆ ---                   ┆ ---                 │
│ str               ┆ str             ┆ i64     ┆ list[i64]             ┆ list[i64]           │
╞═══════════════════╪═════════════════╪═════════╪═══════════════════════╪═════════════════════╡
│ 11 - San Diego    ┆ Imperial Valley ┆ 751     ┆ [0, 0, … 40]          ┆ [0, 0, … 0]         │
│                   ┆ Transit         ┆         ┆                       ┆                     │
│ 11 - San Diego    ┆ Yuma            ┆ 1027    ┆ [0, 0, … 0]           ┆ [0, 0, … 0]         │
│ 11 - San Diego    ┆ North County    ┆ 8650    ┆ [42, 0, … 1085]       ┆ [24, 0, … 481]      │
│ 11 - San Diego    ┆ San Diego       ┆ 46499   ┆ [6560, 2165, … 14151] ┆ [1490, 410, … 3152] │
└───────────────────┴─────────────────┴─────────┴───────────────────────┴─────────────────────┘, _body=<great_tables._gt_data.Body object at 0x7ff256a9d0d0>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='left', column_width=None), ColInfo(var='name', type=<ColInfoTypeEnum.default: 1>, column_label='Operator', column_align='left', column_width=None), ColInfo(var='n_trips', type=<ColInfoTypeEnum.default: 1>, column_label='Weekly Trips', column_align='right', column_width=None), ColInfo(var='weekday_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekday Arrivals', column_align='center', column_width=None), ColInfo(var='weekend_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekend Arrivals', column_align='center', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=3, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Transit Arrivals by the Hour', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=0, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#ffffff')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=1, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#fefeff')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=2, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#dfe9f2')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=3, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#4682b4')])], _locale=<great_tables._gt_data.Locale object at 0x7ff2220f8790>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7ff2220ef590>, <great_tables._gt_data.FormatInfo object at 0x7ff221b6da90>, <great_tables._gt_data.FormatInfo object at 0x7ff221b6cd50>], _substitutions=[<great_tables._gt_data.FormatInfo object at 0x7ff221b89090>], _options=Options(table_id=OptionsInfo(scss=False, category='table

## 12 - Irvine

GT(_tbl_data=shape: (3, 5)
┌───────────────────┬────────────────┬─────────┬──────────────────────┬──────────────────────┐
│ caltrans_district ┆ name           ┆ n_trips ┆ weekday_arrivals     ┆ weekend_arrivals     │
│ ---               ┆ ---            ┆ ---     ┆ ---                  ┆ ---                  │
│ str               ┆ str            ┆ i64     ┆ list[i64]            ┆ list[i64]            │
╞═══════════════════╪════════════════╪═════════╪══════════════════════╪══════════════════════╡
│ 12 - Irvine       ┆ Laguna Beach   ┆ 1302    ┆ [0, 0, … 0]          ┆ [0, 0, … 0]          │
│ 12 - Irvine       ┆ OCTA           ┆ 19673   ┆ [5625, 1805, … 9595] ┆ [1659, 653, … 2403]  │
│ 12 - Irvine       ┆ Anaheim Resort ┆ 51304   ┆ [6165, 5012, … 6955] ┆ [2438, 1996, … 2796] │
└───────────────────┴────────────────┴─────────┴──────────────────────┴──────────────────────┘, _body=<great_tables._gt_data.Body object at 0x7ff256ad38d0>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='left', column_width=None), ColInfo(var='name', type=<ColInfoTypeEnum.default: 1>, column_label='Operator', column_align='left', column_width=None), ColInfo(var='n_trips', type=<ColInfoTypeEnum.default: 1>, column_label='Weekly Trips', column_align='right', column_width=None), ColInfo(var='weekday_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekday Arrivals', column_align='center', column_width=None), ColInfo(var='weekend_arrivals', type=<ColInfoTypeEnum.default: 1>, column_label='Weekend Arrivals', column_align='center', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Transit Arrivals by the Hour', subtitle=None, preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=0, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#ffffff')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=1, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#bbd1e3')]), StyleInfo(locname='data', locnum=5, grpname=None, colname='n_trips', rownum=2, colnum=None, styles=[CellStyleText(color='#000000', font=None, size=None, align=None, v_align=None, style=None, weight=None, stretch=None, decorate=None, transform=None, whitespace=None), CellStyleFill(color='#4682b4')])], _locale=<great_tables._gt_data.Locale object at 0x7ff221b33c10>, _formats=[<great_tables._gt_data.FormatInfo object at 0x7ff221b33e50>, <great_tables._gt_data.FormatInfo object at 0x7ff221b8bc50>, <great_tables._gt_data.FormatInfo object at 0x7ff221b88590>], _substitutions=[<great_tables._gt_data.FormatInfo object at 0x7ff221b8a290>], _options=Options(table_id=OptionsInfo(scss=False, category='table', type='value', value=None), table_caption=OptionsInfo(scss=False, category='table', type='value', value=None), table_width=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_layout=OptionsInfo(scss=True, category='table', type='value', value='fixed'), table_margin_left=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_margin_right=OptionsInfo(scss=True, category='table', type='px', value='auto'), table_background_color=OptionsInfo(scss=True, category='table', type='value', value='white'), table_font_names=OptionsInfo(scss=False, c